In [1]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np

In [2]:
df = pd.read_csv('Data/dds_ch2_nyt/nyt1.csv')

## Initial Overview of the Data

This data frame represents one (simulated) day's worth of ads shown and clicks recorded on the New York Times home page in May 2012. Each row represents a single user, and shows their age, gender (0=Female, 1=Male), number of impressions and clicks, and whether they were signed in.

#TODO: how can you aggregate 'signed in'?

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 458441 entries, 0 to 458440
Data columns (total 5 columns):
 #   Column       Non-Null Count   Dtype
---  ------       --------------   -----
 0   Age          458441 non-null  int64
 1   Gender       458441 non-null  int64
 2   Impressions  458441 non-null  int64
 3   Clicks       458441 non-null  int64
 4   Signed_In    458441 non-null  int64
dtypes: int64(5)
memory usage: 17.5 MB


In [4]:
df.sample(10)

Age  Gender  Impressions  Clicks  Signed_In
155933   35       0            6       0          1
226534   54       1            8       0          1
328468   38       1            1       0          1
301937    0       0            5       1          0
47743     0       0            7       0          0
113275   48       0            6       0          1
416821   41       0            3       0          1
95958    20       0            8       0          1
361107   65       1            4       1          1
175261    0       0            5       1          0

The youngest age is 0, which seems odd. It also seems to be aligned with people who are not signed in. Let's explore that:

In [5]:
df[['Signed_In']].value_counts()

Signed_In
1            321335
0            137106
dtype: int64

In [6]:
df[df['Signed_In'] == 0].describe().round(2)

Age    Gender  Impressions     Clicks  Signed_In
count  137106.0  137106.0    137106.00  137106.00   137106.0
mean        0.0       0.0         5.00       0.14        0.0
std         0.0       0.0         2.24       0.39        0.0
min         0.0       0.0         0.00       0.00        0.0
25%         0.0       0.0         3.00       0.00        0.0
50%         0.0       0.0         5.00       0.00        0.0
75%         0.0       0.0         6.00       0.00        0.0
max         0.0       0.0        18.00       4.00        0.0

Sure enough, we see that non-signed in users have no age and no gender information. Let's look at the data for only the signed in users. Note that it doesn't make sense to call 'describe' on the 'Gender' column, so we'll exclude it using a temporary drop:

In [7]:
df[df['Signed_In'] == 1].drop(columns=['Gender']).describe().round(2)

Age  Impressions     Clicks  Signed_In
count  321335.00    321335.00  321335.00   321335.0
mean       42.06         5.01       0.07        1.0
std        16.31         2.24       0.27        0.0
min         7.00         0.00       0.00        1.0
25%        29.00         3.00       0.00        1.0
50%        41.00         5.00       0.00        1.0
75%        53.00         6.00       0.00        1.0
max       108.00        20.00       3.00        1.0

It is interesting that the maximum impressions for not signed in and for signed in users is 18 and 20, respectively. This is quite a low number. Similarly, the maximum number of clicks for not signed in versus signed in users is 4, 3.

Let's create an Age_Group column which groups users into age buckets. We will use the following age groups:

- < 18
- 18-24
- 25-34
- 35-44
- 45-54
- 55-64
-65+

Note that we might later want to remove all users which are not signed in. But let's include them for now:

In [8]:
bins = [0, 18, 25, 35, 45, 55, 65, 110]
age_labels=['<18', '18-24', '25-34', '35-44', '45-54', '55-64', '65+']
df['Age_Group'] = pd.cut(df['Age'], bins=bins, labels=age_labels, right=False)

Let's view a sample of the data and verify that the numbers look correct. Then let's check the counts per age group

In [9]:
df.sample(10)

Age  Gender  Impressions  Clicks  Signed_In Age_Group
99280    62       1            4       0          1     55-64
413783   29       0            1       0          1     25-34
29866    41       0            4       0          1     35-44
297714    0       0            8       0          0       <18
284048    0       0            3       0          0       <18
397131   29       1            9       0          1     25-34
410782    0       0            6       0          0       <18
143898   70       0            8       0          1       65+
329460   62       0            3       0          1     55-64
384734   41       0            2       0          1     35-44

In [10]:
df[['Age_Group']].value_counts()

Age_Group
<18          150934
35-44         70860
45-54         64288
25-34         58174
55-64         44738
18-24         40694
65+           28753
dtype: int64

Let's add a Click Through Rate column, as this is a common and interesting metric. It is defined as # clicks / # impressions.

It should be impossible to have a click without an impression. Let's quickly just check that this assumption holds (all values should be 0): 

In [11]:
df[df['Impressions'] == 0]['Clicks'].describe()

count    3066.0
mean        0.0
std         0.0
min         0.0
25%         0.0
50%         0.0
75%         0.0
max         0.0
Name: Clicks, dtype: float64

Our assumption holds. Now we can go ahead and create our CTR column:

In [47]:
df['CTR'] = (df['Clicks'] / df['Impressions']) * 100
df.sample(10).round(2)

Age  Gender  Impressions  Clicks  Signed_In Age_Group   CTR  \
15266    61       1            4       1          1     55-64  25.0   
100340   35       1            7       0          1     35-44   0.0   
120662   28       0            4       0          1     25-34   0.0   
415889   46       1            4       0          1     45-54   0.0   
350165   27       0            7       0          1     25-34   0.0   
296062   31       1            4       1          1     25-34  25.0   
310373    0       0            4       0          0       <18   0.0   
227372   61       0            5       0          1     55-64   0.0   
58867    36       1            5       0          1     35-44   0.0   
89171    47       1            4       0          1     45-54   0.0   

               Click_Behaviour  
15266      Impressions; Clicks  
100340  Impressions; No clicks  
120662  Impressions; No clicks  
415889  Impressions; No clicks  
350165  Impressions; No clicks  
296062     Impressions; Clicks  
310373  Impressions; No clicks  
227372  Impressions; No clicks  
58867   Impressions; No clicks  
89171   Impressions; No clicks

You might find that in your sample, all the CTRs are 0. This is quite common, and we know there must be at least some non-zero values as we have non-zero click values. But if you'd like to sanity check it, you can describe the column, to make sure that not all CTR values are 0

In [48]:
df[['CTR']].describe()

CTR
count  455375.000000
mean        1.847053
std         6.903449
min         0.000000
25%         0.000000
50%         0.000000
75%         0.000000
max       100.000000

## Visualising the Data

Let's start by plotting the distributions of impressions and click through rate (CTR) per age group:

In [ ]:
for l in age_labels:
    print(f'Impressions and CTR for the {l} age group')
    
    for col in ['Impressions', 'CTR']:
    
        fig = go.Figure()
        fig.add_trace(
            go.Histogram(x=df[df['Age_Group'] == l][col])
        )
        fig.update_layout(
            xaxis_title_text=col,
            yaxis_title_text='Count',
        )
        fig.show()

Let's create a variable based on click behaviour

In [49]:
def conditions(data: pd.DataFrame):
    if data['Impressions'] == 0:
        return 'No impressions'
    else:
        if data['Clicks'] == 0:
            return 'Impressions; No clicks'
        else:
            return 'Impressions; Clicks'

df['Click_Behaviour'] = df.apply(conditions, axis=1)

display(df.sample(20))
df['Click_Behaviour'].value_counts()

Age  Gender  Impressions  Clicks  Signed_In Age_Group  CTR  \
174546   27       0            4       0          1     25-34  0.0   
138256   52       1            2       0          1     45-54  0.0   
56616    33       0            4       0          1     25-34  0.0   
248460    0       0           10       0          0       <18  0.0   
156473   56       0            4       0          1     55-64  0.0   
303826   19       1            3       0          1     18-24  0.0   
173010   25       1            5       0          1     25-34  0.0   
835      50       1            7       0          1     45-54  0.0   
452190   32       1            3       0          1     25-34  0.0   
276572    0       0            2       0          0       <18  0.0   
130702    0       0            4       0          0       <18  0.0   
12587    36       1            2       0          1     35-44  0.0   
98458    35       0            7       0          1     35-44  0.0   
106925    0       0            4       0          0       <18  0.0   
207011    0       0            6       0          0       <18  0.0   
78061    38       0            2       0          1     35-44  0.0   
70940     0       0            2       0          0       <18  0.0   
110089   28       1            3       0          1     25-34  0.0   
287663   32       1            6       0          1     25-34  0.0   
382013   32       0            5       0          1     25-34  0.0   

               Click_Behaviour  
174546  Impressions; No clicks  
138256  Impressions; No clicks  
56616   Impressions; No clicks  
248460  Impressions; No clicks  
156473  Impressions; No clicks  
303826  Impressions; No clicks  
173010  Impressions; No clicks  
835     Impressions; No clicks  
452190  Impressions; No clicks  
276572  Impressions; No clicks  
130702  Impressions; No clicks  
12587   Impressions; No clicks  
98458   Impressions; No clicks  
106925  Impressions; No clicks  
207011  Impressions; No clicks  
78061   Impressions; No clicks  
70940   Impressions; No clicks  
110089  Impressions; No clicks  
287663  Impressions; No clicks  
382013  Impressions; No clicks

Impressions; No clicks    415537
Impressions; Clicks        39838
No impressions              3066
Name: Click_Behaviour, dtype: int64

So we see that a small portion of users have 0 impressions. The vast majority have impressions but no clicks, which is quite common.

Let's now make some comparisons across user segments. We'll start by looking at the distribution of users for each age group and gender: 
For this we will take only the logged in users, as otherwise age and gender are always 0:

In [16]:
df_signed_in = df[df['Signed_In'] == 1]
df_signed_in.shape

(321335, 8)

In [17]:
df_gender_by_age = (df_signed_in[['Age_Group', 'Gender']]
                    .groupby(['Age_Group', 'Gender'])
                    .size()
                    .reset_index()
                    .rename(columns={0: 'Count'}))
display(df_gender_by_age)
# Sanity check: our total counts equal the length of the data from which they were derived
assert sum(df_gender_by_age['Count']) == len(df_signed_in)

Age_Group  Gender  Count
0        <18       0   4358
1        <18       1   9470
2      18-24       0  18973
3      18-24       1  21721
4      25-34       0  27216
5      25-34       1  30958
6      35-44       0  33184
7      35-44       1  37676
8      45-54       0  30281
9      45-54       1  34007
10     55-64       0  20750
11     55-64       1  23988
12       65+       0  18308
13       65+       1  10445

In [ ]:
fig = go.Figure(data=[
    go.Bar(name='Gender=0 (Female)', x=age_labels, y=df_gender_by_age[df_gender_by_age['Gender'] == 0]['Count']),
    go.Bar(name='Gender=1 (Male)', x=age_labels, y=df_gender_by_age[df_gender_by_age['Gender'] == 1]['Count'])
])
fig.update_layout(
    title_text='Count of users per age group and gender', xaxis_title='Age Group', yaxis_title='Count', barmode='group'
)
fig.show()

Now let's view metrics per age group and gender. We'll start with sum of impressions and clicks, and we'll need to recalculate CTR:

In [50]:
# Sum metrics per age group and gender; recalculate CTR
df_metrics_summed = (df_signed_in[['Age_Group', 'Gender', 'Impressions', 'Clicks']]
                                .groupby(['Age_Group', 'Gender'])
                                # Avoid pandas warning by specifying behaviour for numeric_only
                                .sum(numeric_only=False)
                                .reset_index()
                                .rename(columns={0: 'Count'}))

df_metrics_summed['CTR'] = (df_metrics_summed['Clicks'] / df_metrics_summed['Impressions']) * 100

# Sanity check our totals again
assert sum(df_metrics_summed['Impressions']) == sum(df_signed_in['Impressions'])
assert sum(df_metrics_summed['Clicks']) == sum(df_signed_in['Clicks'])
df_metrics_summed

Age_Group  Gender  Impressions  Clicks       CTR
0        <18       0        21800     683  3.133028
1        <18       1        47439    1382  2.913215
2      18-24       0        95057    1002  1.054104
3      18-24       1       108528    1165  1.073456
4      25-34       0       136292    1388  1.018402
5      25-34       1       154219    1549  1.004416
6      35-44       0       166324    1707  1.026310
7      35-44       1       189500    1955  1.031662
8      45-54       0       151650    1542  1.016815
9      45-54       1       170459    1690  0.991441
10     55-64       0       104220    2105  2.019766
11     55-64       1       120468    2451  2.034565
12       65+       0        91956    2765  3.006873
13       65+       1        52164    1585  3.038494

In [ ]:
for metric in ['Impressions', 'Clicks']:
    fig = go.Figure(data=[
        go.Bar(name='Gender=0 (Female)', x=age_labels, y=df_metrics_summed[df_metrics_summed['Gender'] == 0][metric]),
        go.Bar(name='Gender=1 (Male)', x=age_labels, y=df_metrics_summed[df_metrics_summed['Gender'] == 1][metric])
    ])
    fig.update_layout(title_text=f'Summed {metric} per age group and gender',
                      barmode='group',
                      xaxis_title='Age Group',
                      yaxis_title=f'Sum of {metric}')
    fig.show()

# TODO: Does what I just did make any sense? The resulting plots are the same
These graphs aren't particularly useful, as they don't factor in the size of the demographic groups. So let's add two columns showing the summed Impressions and Clicks per demographic group, as a proportion of the total Impressions and Clicks of the entire dataset. Then we'll recreate our plots:

In [ ]:
for col in ['Impressions', 'Clicks']:
    df_metrics_summed[f'{col}_Proportion'] = df_metrics_summed[col] / sum(df_metrics_summed[col])
df_metrics_summed

In [ ]:
# Sanity check on a couple of these numbers:
print(round(21800 / sum(df_signed_in['Impressions']), 6)) # <18, Gender=0, Impressions, should produce 0.013540
print(round(1585 / sum(df_signed_in['Clicks']), 6)) # 65+, Gender=1, Clicks, should produce 0.069006

Now we can plot the relative metrics:

In [ ]:
for metric in ['Impressions_Proportion', 'Clicks_Proportion']:
    fig = go.Figure(data=[
        go.Bar(name='Gender=0 (Female)', x=age_labels, y=df_metrics_summed[df_metrics_summed['Gender'] == 0][metric]),
        go.Bar(name='Gender=1 (Male)', x=age_labels, y=df_metrics_summed[df_metrics_summed['Gender'] == 1][metric])
    ])
    fig.update_layout(title_text=f'Summed {metric} per age group and gender',
                      barmode='group',
                      xaxis_title='Age Group',
                      yaxis_title=f'Sum of {metric}')
    fig.show()

In [51]:
# It doesn't make sense to speak of a sum of CTR, so we'll display this separately so it has more meaningful titles
fig = go.Figure(data=[
    go.Bar(name='Gender=0 (Female)', x=age_labels, y=df_metrics_summed[df_metrics_summed['Gender'] == 0]['CTR']),
    go.Bar(name='Gender=1 (Male)', x=age_labels, y=df_metrics_summed[df_metrics_summed['Gender'] == 1]['CTR'])
])
fig.update_layout(title_text='CTR per age group and gender', barmode='group', xaxis_title='Age Group', yaxis_title='CTR')
fig.show()

In [22]:
# TODO: Need a graph for this
df_behave_by_demo = (df_signed_in[['Age_Group', 'Gender', 'Click_Behaviour']]
                     .groupby(['Age_Group', 'Gender', 'Click_Behaviour'])
                     .size()
                     .reset_index()
                     .rename(columns={0: 'Count'}))
display(df_behave_by_demo)
# Sanity check: our total counts equal the length of the data from which they were derived
assert sum(df_behave_by_demo['Count']) == len(df_signed_in)

Age_Group  Gender         Click_Behaviour  Count
0        <18       0     Impressions; Clicks    648
1        <18       0  Impressions; No clicks   3684
2        <18       0          No impressions     26
3        <18       1     Impressions; Clicks   1285
4        <18       1  Impressions; No clicks   8115
5        <18       1          No impressions     70
6      18-24       0     Impressions; Clicks    977
7      18-24       0  Impressions; No clicks  17855
8      18-24       0          No impressions    141
9      18-24       1     Impressions; Clicks   1130
10     18-24       1  Impressions; No clicks  20446
11     18-24       1          No impressions    145
12     25-34       0     Impressions; Clicks   1361
13     25-34       0  Impressions; No clicks  25690
14     25-34       0          No impressions    165
15     25-34       1     Impressions; Clicks   1509
16     25-34       1  Impressions; No clicks  29241
17     25-34       1          No impressions    208
18     35-44       0     Impressions; Clicks   1675
19     35-44       0  Impressions; No clicks  31290
20     35-44       0          No impressions    219
21     35-44       1     Impressions; Clicks   1917
22     35-44       1  Impressions; No clicks  35512
23     35-44       1          No impressions    247
24     45-54       0     Impressions; Clicks   1494
25     45-54       0  Impressions; No clicks  28563
26     45-54       0          No impressions    224
27     45-54       1     Impressions; Clicks   1645
28     45-54       1  Impressions; No clicks  32143
29     45-54       1          No impressions    219
30     55-64       0     Impressions; Clicks   2006
31     55-64       0  Impressions; No clicks  18626
32     55-64       0          No impressions    118
33     55-64       1     Impressions; Clicks   2331
34     55-64       1  Impressions; No clicks  21499
35     55-64       1          No impressions    158
36       65+       0     Impressions; Clicks   2598
37       65+       0  Impressions; No clicks  15585
38       65+       0          No impressions    125
39       65+       1     Impressions; Clicks   1486
40       65+       1  Impressions; No clicks   8887
41       65+       1          No impressions     72

In [23]:
# Sanity check: there are apparently 26 people <18 with Gender 0 and No impressions. Is that what we get here?
assert len(df_signed_in[
    (df_signed_in['Age_Group'] == '<18') & 
    (df_signed_in['Gender'] == 0)  & 
    (df_signed_in['Impressions'] == 0)]) == 26

The following graph explores Impressions per age group. Since a user doesn't have to be signed in to get an impression, we can use the entire dataframe, not just the signed in users. However, see the caveat, below...

In [52]:
# TODO UPDATE COMMENT Average metrics per age group and gender
df_imp_counts = (df[['Age_Group', 'Impressions']]
                  .groupby(['Age_Group'])
                  .value_counts()
                  .reset_index()
                  .rename(columns={0: 'Count'}))


display(df_imp_counts.sample(5))

bars_data = []
for label in age_labels:
    bars_data.append(go.Bar(name=f'Age_Group={label}', x=sorted(df_imp_counts['Impressions'].unique()), y=df_imp_counts[df_imp_counts['Age_Group'] == label]['Count']))

fig = go.Figure(data=bars_data)

fig.update_layout(title_text='Impression Counts Per Age Group for All Users',
                  barmode='group',
                  xaxis_title='Number of Impressions',
                  yaxis_title='Count')
fig.show()

Age_Group  Impressions  Count
127       65+            9   1074
112     55-64           12    156
37      18-24           17      2
41      25-34            4  10242
107     55-64            9   1691

The problem with this graph is it appears that people under 18 have the most impressions overall. But we know that actually anyone can fall into this group, as long as they're not signed in. So let's compare the results if we only include signed-in users:

In [33]:
df_imp_counts_signed = (df_signed_in[['Age_Group', 'Impressions']]
                          .groupby(['Age_Group'])
                          .value_counts()
                          .reset_index()
                          .rename(columns={0: 'Count'}))

bars_data = []
for label in age_labels:
    bars_data.append(go.Bar(name=f'Age_Group={label}',
                            x=sorted(df_imp_counts['Impressions'].unique()),
                            y=df_imp_counts_signed[df_imp_counts_signed['Age_Group'] == label]['Count']))

fig = go.Figure(data=bars_data)

fig.update_layout(title_text='Impression Counts Per Age Group for All Users',
                  barmode='group',
                  xaxis_title='Number of Impressions',
                  yaxis_title='Count')
fig.show()

In [46]:
# TODO: That looks really suss, come back to it. Maybe it's fine because of CLT?
# Maybe this is better...
# Nope, different results to the above, what's going on? Maybe the above ones are wrong.

bars_data = []
for label in age_labels:
    bars_data.append(go.Histogram(x=df_signed_in[df_signed_in['Age_Group'] == label]['Impressions'],
                                  name=f'Age_Group={label}'))

fig = go.Figure(data=bars_data)


#fig.update_layout(title_text='Impression Counts Per Age Group for All Users',
#                  barmode='group',
#                  xaxis_title='Number of Impressions',
#                  yaxis_title='Count')
fig.show()

The following graph explores clicks per age group. Since a user doesn't have to be signed in to click or not click, we can use the entire dataframe, not just the signed in users. However, see the caveat, below...

In [27]:
# TODO UPDATE COMMENT Average metrics per age group and gender; recalculate CTR
df_click_counts = (df[['Age_Group', 'Clicks']]
                  .groupby(['Age_Group'])
                  .value_counts()
                  .reset_index()
                  .rename(columns={0: 'Count'}))


display(df_click_counts.sample(5))

bars_data = []
for label in age_labels:
    bars_data.append(go.Bar(name=f'Age_Group={label}', x=[0, 1, 2, 3], y=df_click_counts[df_click_counts['Age_Group'] == label]['Count']))

fig = go.Figure(data=bars_data)

fig.update_layout(title_text='Click Counts Per Age Group for All Users',
                  barmode='group',
                  xaxis_title='Number of Clicks',
                  yaxis_title='Count')
fig.show()

Age_Group  Clicks  Count
4        <18       4      9
12     25-34       2     67
19     35-44       4      0
5      18-24       0  38587
8      18-24       4      0

The problem with this graph is it appears that people under 18 click the most overall. But we know that actually anyone can fall into this group, as long as they're not signed in. So let's compare the results if we only include signed-in users:

In [28]:
df_click_counts_signed = (df_signed_in[['Age_Group', 'Clicks']]
                          .groupby(['Age_Group'])
                          .value_counts()
                          .reset_index()
                          .rename(columns={0: 'Count'}))

bars_data = []
for label in age_labels:
    bars_data.append(go.Bar(name=f'Age_Group={label}',
                            x=[0, 1, 2, 3],
                            y=df_click_counts_signed[df_click_counts_signed['Age_Group'] == label]['Count']))

fig = go.Figure(data=bars_data)

fig.update_layout(title_text='Click Counts Per Age Group for All Users',
                  barmode='group',
                  xaxis_title='Number of Clicks',
                  yaxis_title='Count')
fig.show()